In [ ]:
# Clone the repositories
'''
!git clone https://github.com/NVlabs/stylegan3
!git clone https://github.com/openai/CLIP
!git clone https://github.com/salesforce/BLIP
'''
# Install the requirements
!pip install torch==2.1.2 torchvision==0.16.2 torchaudio==2.1.2 ninja==1.11.1.1
!pip install ftfy==6.1.3 regex==2023.12.25 tqdm==4.66.2
!pip install transformers timm==0.9.16 fairscale==0.4.13
!pip install pip install diffusers
!pip install --upgrade transformers
!pip install --upgrade diffusers
!pip install accelerate
'''
# Download the pre-trained models
!mkdir pretrained_models
'''
# Download dataset:
!gdown -O dataset.zip https://drive.google.com/uc?id=1JtRIbZDuZlBEA6vp870eW3ei0r32uYqF
# https://drive.google.com/file/d/1JtRIbZDuZlBEA6vp870eW3ei0r32uYqF/view?usp=sharing
!unzip -q dataset.zip

!gdown -O dataset2.zip https://drive.google.com/uc?id=1opIDLclS5g0GBG8xGwlTtYL2sa8YKxnV
#1opIDLclS5g0GBG8xGwlTtYL2sa8YKxnV
'''
!curl -L --output pretrained_models/stylegan2-ffhq-512x512.pkl 'https://api.ngc.nvidia.com/v2/models/org/nvidia/team/research/stylegan2/1/files?redirect=true&path=stylegan2-ffhq-512x512.pkl'
!curl -L --output pretrained_models/ViT-B-32.pt 'https://openaipublic.azureedge.net/clip/models/40d365715913c9da98579312b702a82c18be219cc2a73407c4526f58eba950af/ViT-B-32.pt'
!curl -L --output pretrained_models/model_base_capfilt_large.pth https://storage.googleapis.com/sfr-vision-language-research/BLIP/models/model_base_capfilt_large.pth
'''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 670.2/670.2 MB 1.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.8/6.8 MB 57.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 54.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.2/307.2 kB 38.5 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_6

"\n!curl -L --output pretrained_models/stylegan2-ffhq-512x512.pkl 'https://api.ngc.nvidia.com/v2/models/org/nvidia/team/research/stylegan2/1/files?redirect=true&path=stylegan2-ffhq-512x512.pkl'\n!curl -L --output pretrained_models/ViT-B-32.pt 'https://openaipublic.azureedge.net/clip/models/40d365715913c9da98579312b702a82c18be219cc2a73407c4526f58eba950af/ViT-B-32.pt'\n!curl -L --output pretrained_models/model_base_capfilt_large.pth https://storage.googleapis.com/sfr-vision-language-research/BLIP/models/model_base_capfilt_large.pth\n"

In [ ]:
import torch
device = "cuda" if torch.cuda.is_available() else "cpu"

from diffusers import StableDiffusionPipeline
# Initialize Stable Diffusion model
pipeline = StableDiffusionPipeline.from_pretrained("CompVis/stable-diffusion-v1-4", use_auth_token="your_hugging_face_token_here")
pipeline = pipeline.to(device)

# read dataset
from tqdm.auto import tqdm
import os
imagess = os.listdir('dataset')
# import txt file as csv file with pandas with comma separator
import pandas as pd
# Read dataset/image_captions_cleaned captions with pandas:
dtype_dict = {'name': str, 'caption': str}
df = pd.read_csv('dataset/image_captions_cleaned.txt', sep=",", header=0, dtype=dtype_dict)
saved_captions = df['caption'].tolist()
df.head()

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Keyword arguments {'use_auth_token': 'your_hugging_face_token_here'} are not expected by StableDiffusionPipeline and will be ignored.


Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

name                                     caption
0  00001                   a man with a black jacket
1  00002  a young child with a very look on his face
2  00003        a woman with a big smile on her face
3  00004                      a man in a white shirt
4  00005            a man with a bandana on his head

In [ ]:
def generate_image(caption, current_time, index = None):
    blipout = caption
    generated_image = pipeline(blipout).images[0]
    # save figure
    if index == None:
        try:
            generated_image.save(f'inference/{current_time}/{caption}.png') # save image
        except:
            try:
                os.mkdir(f'inference/{current_time}')
                generated_image.save(f'inference/{current_time}/{caption}.png') # save image
            except:
                os.mkdir('./inference')
                os.mkdir(f'inference/{current_time}')
                generated_image.save(f'inference/{current_time}/{caption}.png') # save image
    elif index != None:
            try:
                generated_image.save(f'inference/{current_time}/{index:05d}.png') # save image
            except:
                try:
                    os.mkdir(f'inference/{current_time}')
                    generated_image.save(f'inference/{current_time}/{index:05d}.png') # save image
                except:
                    os.mkdir('./inference')
                    os.mkdir(f'inference/{current_time}')
                    generated_image.save(f'inference/{current_time}/{index:05d}.png') # save image

In [ ]:
current_time = 'stable-diffusion'
index = 0
for idx in tqdm(saved_captions):
    index += 1
    generate_image(idx, current_time, index = index)

import os
print(str(len(os.listdir('/content/inference/'+current_time)))+' images are saved.')

  0%|          | 0/2048 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

...

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

In [20]:
!cd inference && zip -r stable-diffusion.zip stable-diffusion/
# To save inference output zip to google drive
from google.colab import drive
drive.mount('/content/drive')
!cp -r /content/inference/stable-diffusion.zip /content/drive/MyDrive/stable-diffusion.zip

  adding: stable-diffusion/ (stored 0%)
  adding: stable-diffusion/00028.png (deflated 0%)
  adding: stable-diffusion/01195.png (deflated 0%)
  adding: stable-diffusion/01462.png (deflated 0%)
  adding: stable-diffusion/01921.png (deflated 0%)
  adding: stable-diffusion/00456.png (deflated 0%)
  adding: stable-diffusion/01895.png (deflated 0%)
  adding: stable-diffusion/00757.png (deflated 0%)
  adding: stable-diffusion/00500.png (deflated 0%)
  adding: stable-diffusion/00813.png (deflated 0%)
  adding: stable-diffusion/00304.png (deflated 0%)
  adding: stable-diffusion/02032.png (deflated 0%)
  adding: stable-diffusion/00778.png (deflated 0%)
  adding: stable-diffusion/00146.png (deflated 0%)
  adding: stable-diffusion/00683.png (deflated 0%)
  adding: stable-diffusion/00242.png (deflated 1%)
  adding: stable-diffusion/01394.png (deflated 0%)
  adding: stable-diffusion/00420.png (deflated 0%)
  adding: stable-diffusion/01214.png (deflated 0%)
  adding: stable-diffusion/00012.png (defl

In [21]:
import os
len(os.listdir('/content/inference/stable-diffusion'))

2048